In [66]:
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.tag import tnt
from nltk.corpus import indian

train_data = indian.tagged_sents('hindi.pos')
tnt_pos_tagger = tnt.TnT()
tnt_pos_tagger.train(train_data)

# Configuring NLTK

Importing and configuring the nltk corpus and functions for Hindi

In [67]:
from pyiwn import pyiwn
iwn = pyiwn.IndoWordNet('hindi')

# Pyiwn
Pyiwn is a Python library which does wordnet lookups. It uses the CFTIB Worndet for Hindi

In [68]:
def postagWord(data):
    """ A function to POS Tag a sentence"""
    tagged_words = (tnt_pos_tagger.tag(word_tokenize(data)))


In [69]:
def list_of_words(data):
    """A function to break the words into a string and remove the sentence ender"""
    tokenized_words = word_tokenize(data)
    final_words = []
    for word in tokenized_words:
        word = word.replace('।',"")
        final_words.append(word)
    return final_words
        


In [73]:

suffixes = {
    1: ["ो", "े", "ू", "ु", "ी", "ि", "ा"],
    2: ["कर", "ाओ", "िए", "ाई", "ाए", "ने", "नी", "ना", "ते", "ीं", "ती", "ता", "ाँ", "ां", "ों", "ें"],
    3: ["ाकर", "ाइए", "ाईं", "ाया", "ेगी", "ेगा", "ोगी", "ोगे", "ाने", "ाना", "ाते", "ाती", "ाता", "तीं", "ाओं", "ाएं", "ुओं", "ुएं", "ुआं"],
    4: ["ाएगी", "ाएगा", "ाओगी", "ाओगे", "एंगी", "ेंगी", "एंगे", "ेंगे", "ूंगी", "ूंगा", "ातीं", "नाओं", "नाएं", "ताओं", "ताएं", "ियाँ", "ियों", "ियां"],
    5: ["ाएंगी", "ाएंगे", "ाऊंगी", "ाऊंगा", "ाइयाँ", "ाइयों", "ाइयां"],
}

def hi_stem(word):
    for L in 5, 4, 3, 2, 1:
        if len(word) > L + 1:
            for suf in suffixes[L]:
                if word.endswith(suf):
                    return word[:-L]
    return word


# Hindi stemmer 
Hindi takes on morphological inflections and thus the worndet lookup. 

In [74]:
f = open('stopwords.txt')
stopwords = f.readlines()
f.close()

# Stopwords
Stop words are function words and do not contribute to meaning of the sentence. Thus inorder to deal with the actual content that matters, stopwords are removed from the given data.

In [103]:

def getWordLemmaDict(sentence):
    wd = {}
    words = list_of_words(sentence)
    words = map(hi_stem,words)
    for word in words:
        syns = iwn.synsets(word)
        if syns == []:
            continue
        syn = syns[0]
        wd[word] = syn.lemma_names()
    return wd



In [148]:
def wordNetCompare(word1,word2,word_dict1,word_dict2):    
            stemmedX= [ hi_stem(x)  for x in word_dict1[word1] ]
            stemmedY = [ hi_stem(x)  for x in word_dict2[word2] ]
            wordNetMatch = [x for x in stemmedX for y in stemmedY if x == y ]
            if wordNetMatch == []:
                return False
            else:
                return True

In [80]:
hi_stem("मारना")

'मार'

In this project, we are not considering all possible senses of the word. We are considering the first possible sense of the word, and corresponding to that we are considering all possible states 


# CITE
+ Cite the urdu parser
+ IITB 
+ Pyiwin
+ XNLI dataset 
+ https://pdfs.semanticscholar.org/ce0e/9e71a0b09cb9227296ceec26c8654a58e5c9.pdf




In [81]:
s1 = open("./../DataSet/s1_dp.txt").read()
s2 = open("./../DataSet/s2_dp.txt").read()


In [82]:
s1 = s1.split("Sentence:")
s2 = s2.split("Sentence:")


s1

In [83]:
dependDictSent1 = []
dependDictSent2 = []

for i in s1:
    wordDictParser= {}
    x = i.split("\n")
    for j in x:
        y = j.split("\t")
        try:
            wordDictParser[y[1]] = y[7]
        except:
            continue
    dependDictSent1.append(wordDictParser)
for i in s2:
    wordDictParser= {}
    x = i.split("\n")
    for j in x:
        y = j.split("\t")
        try:
            wordDictParser[y[1]] = y[7]
        except:
            continue
    dependDictSent2.append(wordDictParser)

In [145]:
f= open("./../DataSet/s1.txt").read()
sent1 = f.split('\n')
f= open("./../DataSet/s2.txt").read()
sent2 = f.split('\n')
f= open("./../DataSet/label.txt").read()
label = f.split('\n\n')
labels = []
for i in label:
    x = i.split(',')
    if x[0] == "contradiction":
        labels.append(False)
    elif x[0] == "entailment":
        labels.append(True)
    else:
        labels.append(False)
        


In [ ]:
results = []
for i in range(1,len(dependDictSent1)):
    s1 = sent1[i]
    s2 = sent2[i]
    val = False
    orgVal = val
    wordDict1 = getWordLemmaDict(s1)
    wordDict2 = getWordLemmaDict(s2)
    print("Here")
    s1 = list_of_words(s1)
    s2 = list_of_words(s2)
    s1 = map(hi_stem,s1)
    s2 = map(hi)
    ncounter = 0
    for word1 in s1:
        if word1 == "नहीं":
            ncounter+=1
    for word2 in s2:
        if word2 == "नहीं":
            ncounter-=1
    
    for word1 in s1:
        if not word1:
            continue
        if word1 == "|" or word1 == '|':
            continue 
#         print("WOrd1",word1)
        for word2 in s2:
            if not word2:
                continue
            if word2 =="|" or word2 == '|':
                continue
#             print("Word2",word2)
            if word1 == "|" or word1 == '' or word2 == "" or word2 == "|":
                continue
            try:
                if word1 == word2:
                    if dependDictSent1[i][word1] == dependDictSent2[i][word2]:
                        val = True
                else:
                    if wordNetCompare(word1,word2,wordDict1,wordDict2):
                         if dependDictSent1[i][word1] == dependDictSent2[i][word2]:
                            val = True
                
            except Exception as e:
                print(str(e))
                print(word1,word2)
                continue
    print(val,ncounter)
    if ncounter == 0:
        val = val
    else:
        if val:
            val = False
        else:
            val = True
        
    if val == labels[i]:
        results.append(True)
    else:
        results.append(False)
    print(results)

Here
False 0
[True]
Here
False 0
[True, False]
Here
False 0
[True, False, True]
Here
False 0
[True, False, True, True]
Here
False 0
[True, False, True, True, False]
Here
False 0
[True, False, True, True, False, True]
Here
False 0
[True, False, True, True, False, True, True]
Here
False 0
[True, False, True, True, False, True, True, False]
Here
False 0
[True, False, True, True, False, True, True, False, True]
Here
False 0
[True, False, True, True, False, True, True, False, True, True]
Here
False 0
[True, False, True, True, False, True, True, False, True, True, False]
Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True]
Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True, True]
Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True, True, False]
Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True, True, False, True]
Here
False 0
[True, False, Tru

Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, False, True]
Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, False, True, True]
Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, False, True, T

Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, False, True, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False, True, True, False, True, True, False]
Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, False, True, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False, True, True, False, True, True, False, True]
Here
False 0
[True, False, True, True, False, True, True, False, T

Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, False, True, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, True, False, True, True, False, False, True, True, False, True, True, True]
Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, False, True, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False, Tru

Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, False, True, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, True, False, True, True, False, False, True, True, False, True, True, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False]
Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, False, True, True, Tru

...

Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, False, True, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, True, False, True, True, False, False, True, True, False, True, True, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False, False, True, True, True, False, True, True, False, True, True, True, False, True, False, True, True, True, False, True, False, True, False, True, True, True, True, False, True, False, True, True, True, False, True, False, True, True, True, False, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False

Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, False, True, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, True, False, True, True, False, False, True, True, False, True, True, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False, False, True, True, True, False, True, True, False, True, True, True, False, True, False, True, True, True, False, True, False, True, False, True, True, True, True, False, True, False, True, True, True, False, True, False, True, True, True, False, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False

Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, False, True, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, True, False, True, True, False, False, True, True, False, True, True, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False, False, True, True, True, False, True, True, False, True, True, True, False, True, False, True, True, True, False, True, False, True, False, True, True, True, True, False, True, False, True, True, True, False, True, False, True, True, True, False, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False

Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, False, True, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, True, False, True, True, False, False, True, True, False, True, True, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False, False, True, True, True, False, True, True, False, True, True, True, False, True, False, True, True, True, False, True, False, True, False, True, True, True, True, False, True, False, True, True, True, False, True, False, True, True, True, False, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False

Here
False 0
[True, False, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, True, False, True, True, True, False, True, False, True, False, True, True, False, True, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False, True, True, False, True, True, False, True, True, True, False, True, True, False, True, True, False, False, True, True, False, True, True, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False, False, True, True, True, False, True, True, False, True, True, True, False, True, False, True, True, True, False, True, False, True, False, True, True, True, True, False, True, False, True, True, True, False, True, False, True, True, True, False, True, True, False, True, False, True, True, False, True, True, True, False, True, True, False

In [138]:
results

[False]